In [1]:
!pip install cached-conv
!pip install GPUtil
!pip install lmdb
!pip install einops
!pip install absl-py
!pip install gin-config
!pip install librosa

  Preparing metadata (setup.py) ... done
  Created wheel for GPUtil: filename=GPUtil-1.4.0-py3-none-any.whl size=7393 sha256=da073e8a04113a8dfc608a3ab94df78cdd39fb60ac4a6e9b7c538f42f94f9bd5
  Stored in directory: /home/jasper/.cache/pip/wheels/a9/8a/bd/81082387151853ab8b6b3ef33426e98f5cbfebc3c397a9d4d0
Successfully built GPUtil
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 299.2/299.2 kB 13.9 MB/s eta 0:00:00


In [2]:
!pip install pytorch_lightning==1.9.0

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 825.8/825.8 kB 901.5 kB/s eta 0:00:000:00:010:00:01:01
  Attempting uninstall: pytorch_lightning
    Found existing installation: pytorch-lightning 2.2.1
    Uninstalling pytorch-lightning-2.2.1:
      Successfully uninstalled pytorch-lightning-2.2.1
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
asteroid 0.7.0 requires pytorch-lightning>=2.0.0, but you have pytorch-lightning 1.9.0 which is incompatible.


In [8]:
!wget https://play.forum.ircam.fr/rave-vst-api/get_model/isis

--2024-03-19 19:23:43--  https://play.forum.ircam.fr/rave-vst-api/get_model/isis
Resolving play.forum.ircam.fr (play.forum.ircam.fr)... 129.102.1.173, 2001:660:3004:4001::ef23:257e
Connecting to play.forum.ircam.fr (play.forum.ircam.fr)|129.102.1.173|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 148725070 (142M) [application/x-download]
Saving to: ‘isis’

isis                100%[===================>] 141.83M  22.2MB/s    in 6.7s    

2024-03-19 19:23:50 (21.2 MB/s) - ‘isis’ saved [148725070/148725070]



In [1]:
%cd RAVE

/home/jasper/Documents/PhD/Y0/conv_tasnet_source_sep/source-resynthesis/RAVE


/home/jasper/miniforge3/envs/tasnet/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [3]:
from absl import app, flags, logging
import pdb
import torch, torchaudio, argparse, os, tqdm, re, gin
import cached_conv as cc
import IPython.display as ipd

import rave

FLAGS = flags.FLAGS
flags.DEFINE_string('model', required=True, default=None, help="model path")
flags.DEFINE_multi_string('input', required=True, default=None, help="model inputs (file or folder)")
flags.DEFINE_string('out_path', 'generations', help="output path")
flags.DEFINE_string('name', None, help="name of the model")
flags.DEFINE_integer('gpu', default=-1, help='GPU to use')
flags.DEFINE_bool('stream', default=False, help='simulates streaming mode')
flags.DEFINE_integer('chunk_size', default=None, help="chunk size for encoding/decoding (default: full file)")

torch.set_float32_matmul_precision('high')
cc.use_cached_conv(False)

In [1]:
# model_path = '/content/RAVE/musicnet.ts'
# model_path = './trained_model/isis.ts'
# model_path = './trained_model/sol_full.ts'
model_path = './trained_model/guitar_iil_b2048_r48000_z16.ts'
f = './test_files/bass.wav'

In [6]:
logging.info("building rave")
is_scripted = False
if not os.path.exists(model_path):
    logging.error('path %s does not seem to exist.'%model_path)
    exit()
if os.path.splitext(model_path)[1] == ".ts":
    model = torch.jit.load(model_path)
    is_scripted = True
else:
    config_path = rave.core.search_for_config(model_path)
    if config_path is None:
        logging.error('config not found in folder %s'%model_path)
    gin.parse_config_file(config_path)
    model = rave.RAVE()
    run = rave.core.search_for_run(model_path)
    if run is None:
        print("run not found in folder %s"%model_path)
        logging.error("run not found in folder %s"%model_path)
    model = model.load_from_checkpoint(run)

device = torch.device('cuda:%d'%0)
model = model.to(device)

In [20]:
x, sr = torchaudio.load(f)
print(f'shape: {x.shape} sr: {sr}, model sr: {model.sr}')

if sr != model.sr:
  x = torchaudio.functional.resample(x, sr, model.sr)
  print('new shape:')
  print(f'shape: {x.shape} sr: {model.sr}, model sr: {model.sr}')

if model.n_channels != x.shape[0]:
  if model.n_channels < x.shape[0]:
      x = x[:model.n_channels]
  else:
      print('[Warning] file %s has %d channels, butt model has %d channels ; skipping'%(f, model.n_channels))
x = x.to(device)

shape: torch.Size([1, 288000]) sr: 8000, model sr: 48000
new shape:
shape: torch.Size([1, 1728000]) sr: 48000, model sr: 48000


In [22]:
x = x.unsqueeze(0)
out = model.forward(x)

In [26]:
ipd.display(ipd.Audio(out[0].cpu().detach().numpy(), rate=model.sr))